#  Tone Classification Task

## Data Preparation

In [72]:
require 'loader'
require 'nn'
MAX_LEN = 256
max_len = 128
-- Loader:new(obj, max_len)
ldr = Loader:new(nil, MAX_LEN)

In [73]:
function moving_avg(vec, window)
    local len = (#vec)[1]
    local new_vec = torch.Tensor(len):fill(0.0)
    for i = 1, (len - window - 1) do
        local sum = vec[{{i, i + window - 1}}]:sum() / window
        new_vec[i+1] = sum
    end
    return new_vec
end

In [74]:
-- kick too large or too small values
function kick(vec, topsmall, toplarge)
    -- kick the smalls
    for i = 1, topsmall do
        vec:csub(vec:min())
        new_vec = vec[vec:gt(0.0)]:clone()
        vec = new_vec
    end
    for i = 1, toplarge do
        _, inds = torch.max(vec, 1)
--         print(inds)
--         for j = 1, (#inds)[1] do
--             vec[inds[j]] = 0.0
--         end
        vec[inds[1]] = 0.0
        vec[inds[-1]] = 0.0
        new_vec = vec[vec:gt(0.0)]:clone()
        vec = new_vec
    end
    return new_vec
end

-- local i = 0
-- local tester = torch.Tensor(10):apply(function() i = i + 1 return i end)
-- print(tester)
-- print(kick(tester, 1, 0))

In [75]:
local matrix = require "matrix"
local fit = {}
local function getresults( mtx )
    assert( #mtx+1 == #mtx[1], "Cannot calculate Results" )
    mtx:dogauss()
    -- tresults
    local cols = #mtx[1]
    local tres = {}
    for i = 1,#mtx do
        tres[i] = mtx[i][cols]
    end
    return unpack( tres )
end

function fit.parabola( x_values,y_values )
    -- x_values = { x1,x2,x3,...,xn }
    -- y_values = { y1,y2,y3,...,yn }

    -- values for A matrix
    local a_vals = {}
    -- values for Y vector
    local y_vals = {}

    for i,v in ipairs( x_values ) do
        a_vals[i] = { 1, v, v*v }
        y_vals[i] = { y_values[i] }
    end

    -- create both Matrixes
    local A = matrix:new( a_vals )
    local Y = matrix:new( y_vals )

    local ATA = matrix.mul( matrix.transpose(A), A )
    local ATY = matrix.mul( matrix.transpose(A), Y )

    local ATAATY = matrix.concath(ATA,ATY)

    return getresults( ATAATY )
end

function fit_quad(vec, targetLen)
    local len = (#vec)[1]
    local xs = {}
    local ys = {}
    local a, b, c
    for i = 1, len do
        table.insert(xs, i)
        table.insert(ys, vec[i])
    end
    a, b, c = fit.parabola(xs, ys)
    local res = torch.Tensor(targetLen)
    for i = 1, targetLen do
        local ii = (i - 1) / (targetLen - 1) * (len - 1) + 1
        res[i] = a + b * ii + c * ii * ii
    end
    return res, {a, b, c}
end

function fit_tail(vec, targetLen, portion)
    local len = (#vec)[1]
    local start = math.modf(len * portion)
    local xs = {}
    local ys = {}
    local a, b, c
    for i = 1, len - start do
        table.insert(xs, i)
        table.insert(ys, vec[i + start])
    end
    a, b, c = fit.parabola(xs, ys)
    local res = torch.Tensor(targetLen)
    for i = 1, targetLen do
        local ii = (i - 1) / (targetLen - 1) * (len - start - 1) + 1
        res[i] = a + b * ii + c * ii * ii
    end
    return res, {a, b, c}
end

In [76]:
function make_linear_spine(vec, targetLen)
    local len = (#vec)[1]
    local ys = {}
    
    for i = 1, len do
        table.insert(ys, vec[i])
    end
    
    local res
    local coef
    res, coef = torch.Tensor(targetLen)
    
    local i = 1
    for ind = 1, targetLen do
        local x = (ind - 1) * (len - 1) / (targetLen - 1) + 1
        if  x > i then
            i = i + 1
        end
        if x == i then 
            res[ind] = ys[i]
        else
            res[ind] = (ys[i] - ys[i - 1]) * (x - i + 1) + ys[i - 1]
        end
    end
    return res, coef
end

# Dataset!

In [84]:
function make_dataset(name, mode)
    local ldr = Loader:new(nil, 256)
    local collection = {data = ldr.data[name]:float(), label = ldr.label[name]}
    function collection:size() 
        return self.data:size(1) 
    end
    
    -- Mel Frequency
    for j = 1, collection:size() do
        collection.data[{j, {}, 1}]:div(700):log1p():mul(5975.208)
    end
    
    -- local standardization
    for i = 1, 2 do
        for j = 1, collection:size() do
            local std = collection.data[{j, {}, i}]:std()
            collection.data[{j, {}, i}]:div(std)
        end
    end

    -- global standardization
    for i = 1, 2 do
        local std = collection.data[{{}, {}, i}]:std()
        collection.data[{{}, {}, i}]:div(std)
    end

    local resized_collection = {
        data = torch.Tensor(collection:size(), max_len,2):float(),
        label = collection.label
    }
    -- filter noice and shif to the beginning
    local coef = {}
    for i = 1, collection:size() do
        for j = 1, 256 do
            if (collection.data[{i, j, 2}] < 1.0) then
                collection.data[{i, j, 1}] = 0.0
                collection.data[{i, j, 2}] = 0.0
            end
        end
        local shifted_F0 = torch.Tensor(max_len):fill(0.0)
        local shifted_Engy = torch.Tensor(max_len):fill(0.0)
        local data = collection.data[{i, {}, {}}]
        local tmpF0 = data[{{}, 1}][data[{{}, 1}]:gt(0.0)]:clone()
        local tmpEngy = data[{{}, 2}][data[{{}, 2}]:gt(0.0)]:clone()
        
        peek = tmpF0
--         smooth (refer to a paper)
--         tmpF0 = tmpF0:csub(tmpF0:min())
--         tmpF0 = tmpF0[tmpF0:gt(0.0)]
--         tmpF0 = tmpF0:index(1 ,torch.linspace((#tmpF0)[1],1,(#tmpF0)[1]):long())
--         local tmpF0_prime = tmpF0:clone()
--         local c_1 = 0.34
--         local c_2 = 0.74
--         -- half or double
--         for j = 2, (#tmpF0)[1] do
--             if math.abs(tmpF0[j] / 2 - tmpF0[j - 1]) < c_1 then 
--                 tmpF0[j] = tmpF0[j] / 2
--             elseif math.abs(2 * tmpF0[j] - tmpF0[j - 1]) < c_1 then
--                 tmpF0[j] = tmpF0[j] * 2
--             end
--         end
--         -- random error
        
--         for j = 3, (#tmpF0)[1] - 1 do
--             if math.abs(tmpF0[j] - tmpF0_prime[j - 1]) > c_1 and math.abs(tmpF0[j + 1] - tmpF0_prime[j - 1]) > c_2 then
--                 tmpF0_prime[j] = 2 * tmpF0_prime[j - 1] - tmpF0_prime[j - 2]
--             elseif math.abs(tmpF0[j] - tmpF0_prime[j - 1]) > c_1 and math.abs(tmpF0[j + 1] - tmpF0_prime[j - 1]) <= c_2 then
--                 tmpF0_prime[j] = 0.5 * (tmpF0_prime[j - 1] + tmpF0[j + 1])
--             else 
--                 tmpF0_prime[j] = tmpF0[j] 
--             end
--         end
--         -- backward check
--         for j = (#tmpF0)[1] - 2, 2, -1 do
--             if math.abs(tmpF0_prime[j] - tmpF0_prime[j + 1]) > c_1 and math.abs(tmpF0_prime[j - 1] - tmpF0_prime[j + 1]) > c_2 then
--                 tmpF0[j] = 2 * tmpF0_prime[j + 1] - tmpF0_prime[j + 2]
--             elseif math.abs(tmpF0_prime[j] - tmpF0_prime[j - 1]) > c_1 and math.abs(tmpF0_prime[j + 1] - tmpF0_prime[j - 1]) <= c_2 then
--                 tmpF0[j] = 0.5 * (tmpF0_prime[j + 1] + tmpF0_prime[j - 1])
--             else 
--                 tmpF0[j] = tmpF0_prime[j]
--             end
--             if math.abs(tmpF0_prime[j] - tmpF0[j]) < c_1 then
--                 for k = 1, j - 1 do
--                     tmpF0[k] = tmpF0_prime[k]
--                 end
--                 break
--             end
--         end
-- --         tmpF0:index(1 ,torch.linspace((#tmpF0)[1],1,(#tmpF0)[1]):long())
        
-- --         tmpF0 = kick(tmpF0, 1, 0)
-- --         tmpEngy = kick(tmpEngy, 1, 0)
        
-- --         local cut_len = (#tmpF0)[1] * 0.25
-- --         tmpF0 = tmpF0[{{cut_len, -1}}]

--         -- smooth
--         tmpF0 = moving_avg(tmpF0, 5)
--         tmpF0 = tmpF0[tmpF0:gt(0.0)]:clone()
--         tmpEngy = moving_avg(tmpEngy, 5)
--         tmpEngy = tmpEngy[tmpEngy:gt(0.0)]:clone()

        if mode == 'shift' then
            shifted_F0[{{2, (#tmpF0)[1] + 1}}] = tmpF0
            shifted_Engy[{{2, (#tmpEngy)[1] + 1}}] = tmpEngy
            resized_collection.data[{i, {}, 1}] = shifted_F0
            resized_collection.data[{i, {}, 2}] = shifted_Engy
        elseif mode == 'quad' then
            resized_collection.data[{i, {}, 1}], coef[i] = fit_quad(tmpF0, max_len)
            resized_collection.data[{i, {}, 2}] = fit_quad(tmpEngy, max_len)
        elseif mode == 'linear' then
            resized_collection.data[{i, {}, 1}] = make_linear_spine(tmpF0, max_len)
            resized_collection.data[{i, {}, 2}] = make_linear_spine(tmpEngy, max_len)
        end
    end
--     for i = 1, 2 do
--         for j = 1, dataset:size() do
--             local std = resized_collection.data[{j, {}, i}]:std()
--             resized_collection.data[{j, {}, i}]:div(std)
--         end
--     end
    for i = 1, 2 do
        for j = 1, collection:size() do
            local mean = resized_collection.data[{j, {}, i}]:mean()
            resized_collection.data[{j, {}, i}]:csub(mean)
--             local mean = resized_collection.data[{j, {}, i}][-1]
--             resized_collection.data[{j, {}, i}]:csub(mean)
--             local std = resized_collection.data[{{}, {}, i}]:std()
--             resized_collection.data[{{}, {}, i}]:div(std)
        end
    end
    for i = 1, 2 do
        local std = resized_collection.data[{{}, {}, i}]:std()
        resized_collection.data[{{}, {}, i}]:div(std)
    end
    
    resized_collection.data[{{}, {}, 2}]:fill(0.0)
    for i = 1, collection:size() do
        resized_collection[i] = {resized_collection.data[i], resized_collection.label[i]}
    end
    print("dataset "..name.." has been constructed!")
    return resized_collection, coef
end

In [85]:
trainset, tarincoef = make_dataset('train', 'linear')
testset, testcoef = make_dataset('test', 'linear')
newtestset, newtestcoef = make_dataset('test_new', 'linear')

dataset train has been constructed!	


dataset test has been constructed!	


dataset test_new has been constructed!	


In [87]:
Plot = require 'itorch.Plot'
local x1 = torch.range(1,max_len)
local sampleN = 400
-- local y2 = newtestset.data[{sampleN,{},2}]
-- local x1 = torch.range(1,18)
-- local y1 = peek
plot = Plot():title('Raw f0 Feature')
for i = 1, sampleN do
    local y1 = trainset.data[{i,{},1}]
    if i <= 100 then plot:line(x1, y1,'red','f0') 
    elseif i <= 200 then plot:line(x1, y1,'blue','f0')
    elseif i <= 300 then plot:line(x1, y1,'green','f0')
    else plot:line(x1, y1,'black','f0') end
end
plot:redraw()

In [69]:
Plot = require 'itorch.Plot'
local sampleN = 400
-- local y2 = newtestset.data[{sampleN,{},2}]
-- local x1 = torch.range(1,18)
-- local y1 = peek
plot = Plot():title('Feature Observation of Tones')
for i = 1, sampleN do
    local x1 = {tarincoef[i][1]}
    local y1 = {tarincoef[i][3]}
    if i <= 100 then plot:circle(x1, y1,'red','f0') 
    elseif i <= 200 then plot:circle(x1, y1,'blue','f0')
    elseif i <= 300 then plot:circle(x1, y1,'green','f0')
    else plot:circle(x1, y1,'black','f0') end
end
plot:redraw()

In [70]:
Plot = require 'itorch.Plot'
local x1 = torch.range(1,max_len)
local sampleN = 226
-- local y2 = newtestset.data[{sampleN,{},2}]
-- local x1 = torch.range(1,18)
-- local y1 = peek
plot = Plot():title('Feature Observation of Tones')
for i = 1, sampleN do
    local y1 = newtestset.data[{i,{},1}]
    if i <= 54 then plot:line(x1, y1,'red','f0')
--     if i <= 54 then 
    elseif i <= 114 then plot:line(x1, y1,'blue','f0')
    elseif i <= 174 then plot:line(x1, y1,'green','f0')
    else plot:line(x1, y1,'black','f0') end
end
plot:redraw()

In [71]:
Plot = require 'itorch.Plot'
local sampleN = 226
-- local y2 = newtestset.data[{sampleN,{},2}]
-- local x1 = torch.range(1,18)
-- local y1 = peek
plot = Plot():title('Feature Observation of Tones')
for i = 1, sampleN do
    local x1 = {newtestcoef[i][2]}
    local y1 = {newtestcoef[i][3]}
    if i <= 54 then plot:circle(x1, y1,'red','f0') 
    elseif i <= 114 then plot:circle(x1, y1,'blue','f0')
    elseif i <= 174 then plot:circle(x1, y1,'green','f0')
    else plot:circle(x1, y1,'black','f0') end
end
plot:redraw()

In [43]:
peek

 2.7582
 2.9331
 3.0379
 3.1390
 3.2025
 3.2660
 3.3295
 3.3930
 3.4565
 3.5200
 3.3657
 3.2113
 3.1614
 3.0501
 2.9771
 2.8889
 2.8337
 2.8231
 2.8037
 2.7307
 2.6745
 2.6150
 2.5463
 2.4992
 2.3712
 2.3180
 2.2314
 2.1570
 2.0885
 2.0196
 1.9625
 1.9148
 1.8748
 1.8422
 1.7960
 1.7475
[torch.FloatTensor of size 36]



# Model

In [9]:
require 'dp'
local inp = 2;  -- dimensionality of one sequence element 
local outp = 4; -- number of derived features for one sequence element
local conv_kw = 4;   -- number of sequence element kernel operates on per step
local conv_dw = 4;   -- step dw and go on to the next sequence element

local pool_kw = 4;   -- number of sequence element pooled on per step
local pool_dw = 4;   -- step dw and go on to the next sequence element

local nOutputFrame = (max_len - conv_kw) / conv_dw + 1
local nOutputFrame = (nOutputFrame - pool_kw) / pool_dw + 1

net = nn.Sequential()
peek = nn.TemporalConvolution(inp, outp, conv_kw, conv_dw)
net:add(peek)
net:add(nn.ReLU())
net:add(nn.TemporalMaxPooling(pool_kw, pool_dw))
net:add(nn.View(outp*nOutputFrame))
net:add(nn.Linear(outp*nOutputFrame, 128))
-- net:add(nn.BatchNormalization(64))
net:add(nn.ReLU())
net:add(nn.Linear(128, 4))
net:add(nn.LogSoftMax())

In [10]:
print (net:__tostring())

nn.Sequential {
  [input -> (1) -> (2) -> (3) -> (4) -> (5) -> (6) -> (7) -> (8) -> output]
  (1): nn.TemporalConvolution
  (2): nn.ReLU
  (3): nn.TemporalMaxPooling
  (4): nn.View(16)
  (5): nn.Linear(16 -> 128)
  (6): nn.ReLU
  (7): nn.Linear(128 -> 4)
  (8): nn.LogSoftMax
}	


In [11]:
criterion = nn.ClassNLLCriterion();  
trainer = nn.StochasticGradient(net, criterion)  
trainer.learningRate = 0.001
trainer.maxIteration = 200
trainer.verbose = False

In [12]:
function cal_acc(dataset)
    local acc = 0.0
    for i = 1, dataset:size() do
        _, output = torch.max(net:forward(dataset[i][1]), 1)
        if output[1] == dataset[i][2] then
            acc = acc + 1.0
        end
    end
    acc = acc / dataset:size()
    return acc
end

In [13]:
recorder = {loss = {}, trainacc = {}, valacc = {}, testacc = {}}
trainer.hookIteration = function(obj, iteration, currentError) 
    local trainacc = cal_acc(trainset)
    local valacc = cal_acc(testset)
    local testacc = cal_acc(newtestset)
    table.insert(recorder.loss, currentError)
    table.insert(recorder.trainacc, trainacc)
    table.insert(recorder.valacc, valacc)
    table.insert(recorder.testacc, testacc)
    if (iteration % 10 == 0) then 
        print('Iteration '..iteration..': loss('..currentError..') train_acc('
            ..trainacc..') test_acc('..valacc..') new_test_acc('..testacc..').')
    end
end

In [14]:
trainer:train(trainset)

...RZ/torch/install/share/lua/5.1/nn/StochasticGradient.lua:19: attempt to call method 'size' (a nil value)
stack traceback:
	...RZ/torch/install/share/lua/5.1/nn/StochasticGradient.lua:19: in function 'f'
	[string "local f = function() return trainer:train(tra..."]:1: in main chunk
	[C]: in function 'xpcall'
	/Users/YRZ/torch/install/share/lua/5.1/itorch/main.lua:210: in function </Users/YRZ/torch/install/share/lua/5.1/itorch/main.lua:174>
	/Users/YRZ/torch/install/share/lua/5.1/lzmq/poller.lua:75: in function 'poll'
	/Users/YRZ/torch/install/share/lua/5.1/lzmq/impl/loop.lua:307: in function 'poll'
	/Users/YRZ/torch/install/share/lua/5.1/lzmq/impl/loop.lua:325: in function 'sleep_ex'
	/Users/YRZ/torch/install/share/lua/5.1/lzmq/impl/loop.lua:370: in function 'start'
	/Users/YRZ/torch/install/share/lua/5.1/itorch/main.lua:389: in main chunk
	[C]: in function 'require'
	(command line):1: in main chunk
	[C]: at 0x01017c5360: 

In [16]:
local x = torch.range(1, #recorder.loss)
plt = Plot():line(x, recorder.loss,'red','loss'):legend(true):title('Train Loss'):draw()
plt = Plot():line(x, recorder.trainacc,'blue','train_acc'):legend(true):title('Accuracy'):draw()
plt:line(x, recorder.valacc,'green','val_acc'):redraw()

bad argument #2 to '?' (upper bound and larger bound incoherent with step sign at /Users/YRZ/torch/pkg/torch/lib/TH/generic/THTensorMath.c:1457)
stack traceback:
	[C]: at 0x0b4ee170
	[C]: in function 'range'
	[string "local x = torch.range(1, #recorder.loss)..."]:1: in main chunk
	[C]: in function 'xpcall'
	/Users/YRZ/torch/install/share/lua/5.1/itorch/main.lua:210: in function </Users/YRZ/torch/install/share/lua/5.1/itorch/main.lua:174>
	/Users/YRZ/torch/install/share/lua/5.1/lzmq/poller.lua:75: in function 'poll'
	/Users/YRZ/torch/install/share/lua/5.1/lzmq/impl/loop.lua:307: in function 'poll'
	/Users/YRZ/torch/install/share/lua/5.1/lzmq/impl/loop.lua:325: in function 'sleep_ex'
	/Users/YRZ/torch/install/share/lua/5.1/lzmq/impl/loop.lua:370: in function 'start'
	/Users/YRZ/torch/install/share/lua/5.1/itorch/main.lua:389: in main chunk
	[C]: in function 'require'
	(command line):1: in main chunk
	[C]: at 0x010b22c360: 

In [17]:
print ('accuracy on train set '..cal_acc(trainset))
print ('accuracy on test set '..cal_acc(testset))
print ('accuracy on new test set '..cal_acc(newtestset))

[string "function cal_acc(dataset)..."]:3: attempt to call method 'size' (a nil value)
stack traceback:
	[string "function cal_acc(dataset)..."]:3: in function 'cal_acc'
	[string "print ('accuracy on train set '..cal_acc(trai..."]:1: in main chunk
	[C]: in function 'xpcall'
	/Users/YRZ/torch/install/share/lua/5.1/itorch/main.lua:210: in function </Users/YRZ/torch/install/share/lua/5.1/itorch/main.lua:174>
	/Users/YRZ/torch/install/share/lua/5.1/lzmq/poller.lua:75: in function 'poll'
	/Users/YRZ/torch/install/share/lua/5.1/lzmq/impl/loop.lua:307: in function 'poll'
	/Users/YRZ/torch/install/share/lua/5.1/lzmq/impl/loop.lua:325: in function 'sleep_ex'
	/Users/YRZ/torch/install/share/lua/5.1/lzmq/impl/loop.lua:370: in function 'start'
	/Users/YRZ/torch/install/share/lua/5.1/itorch/main.lua:389: in main chunk
	[C]: in function 'require'
	(command line):1: in main chunk
	[C]: at 0x010b22c360: 

## To see why

In [18]:
mislabeled = {}
local output
for i = 1, newtestset:size() do
    _, output = torch.max(net:forward(newtestset[i][1]), 1)
    if output[1] ~= newtestset[i][2] then
        table.insert(mislabeled, { data_id = i, pred = output[1], gt = newtestset[i][2]})
    end
end

[string "mislabeled = {}..."]:3: attempt to call method 'size' (a nil value)
stack traceback:
	[string "mislabeled = {}..."]:3: in main chunk
	[C]: in function 'xpcall'
	/Users/YRZ/torch/install/share/lua/5.1/itorch/main.lua:210: in function </Users/YRZ/torch/install/share/lua/5.1/itorch/main.lua:174>
	/Users/YRZ/torch/install/share/lua/5.1/lzmq/poller.lua:75: in function 'poll'
	/Users/YRZ/torch/install/share/lua/5.1/lzmq/impl/loop.lua:307: in function 'poll'
	/Users/YRZ/torch/install/share/lua/5.1/lzmq/impl/loop.lua:325: in function 'sleep_ex'
	/Users/YRZ/torch/install/share/lua/5.1/lzmq/impl/loop.lua:370: in function 'start'
	/Users/YRZ/torch/install/share/lua/5.1/itorch/main.lua:389: in main chunk
	[C]: in function 'require'
	(command line):1: in main chunk
	[C]: at 0x010b22c360: 

In [19]:
print(#mislabeled)

0	


In [20]:
print(mislabeled)

In [21]:
print(net:forward(newtestset[4][1]))
-- print(peek:forward(newtestset[4][1]))
print(peek.weight)
-- local x1 = torch.range(1, MAX_LEN - 1)
-- local sampleN = 7
-- local y1 = newtestset.data[{sampleN,{},1}]
-- local y2 = peek
-- plot = Plot():line(x1, y1,'red','f0'):legend(true):title('Feature Observation of a Tone '..newtestset.label[sampleN]):draw()
-- plot:line(x1, y2,'blue','engy'):redraw()

/Users/YRZ/torch/install/share/lua/5.1/nn/Container.lua:67: 
In 1 module of nn.Sequential:
/Users/YRZ/torch/install/share/lua/5.1/nn/THNN.lua:110: bad argument #3 to 'v' (cannot convert 'struct THDoubleTensor *' to 'struct THFloatTensor *')
stack traceback:
	[C]: in function 'v'
	/Users/YRZ/torch/install/share/lua/5.1/nn/THNN.lua:110: in function 'TemporalConvolution_updateOutput'
	...Z/torch/install/share/lua/5.1/nn/TemporalConvolution.lua:41: in function <...Z/torch/install/share/lua/5.1/nn/TemporalConvolution.lua:40>
	[C]: in function 'xpcall'
	/Users/YRZ/torch/install/share/lua/5.1/nn/Container.lua:63: in function 'rethrowErrors'
	/Users/YRZ/torch/install/share/lua/5.1/nn/Sequential.lua:44: in function 'forward'
	[string "print(net:forward(newtestset[4][1]))..."]:1: in main chunk
	[C]: in function 'xpcall'
	/Users/YRZ/torch/install/share/lua/5.1/itorch/main.lua:210: in function </Users/YRZ/torch/install/share/lua/5.1/itorch/main.lua:174>
	/Users/YRZ/torch/install/share/lua/5.1/lzmq

## Try Rules!

In [22]:
function cal_acc_rule(dataset)
    local acc = 0.0
    for i = 1, dataset:size() do
        output = simple_rule(dataset[i][1])
        if output == dataset[i][2] then
            acc = acc + 1.0
        end
    end
    acc = acc / dataset:size()
    return acc
end

In [23]:
function simple_rule(example)
    -- only take f0
    local f0 = example[{{}, 1}]
    local max = f0:max()
    if max < 0.3 then return 1 end
    local totcnt = 0
    local cnt = 0
    for i = 1, (#f0)[1] - 1 do
        if f0[i + 1] ~= 0 then totcnt = totcnt + 1 end
        if f0[i + 1] - f0[i] < 0 then cnt = cnt + 1 end
    end
    if cnt > 0.8 * totcnt then return 4
    elseif cnt < 0.2 * totcnt then return 2
    else return 3 end
end

In [24]:
print ('accuracy on train set '..cal_acc_rule(trainset))
print ('accuracy on test set '..cal_acc_rule(testset))
print ('accuracy on new test set '..cal_acc_rule(newtestset))

[string "function cal_acc_rule(dataset)..."]:3: attempt to call method 'size' (a nil value)
stack traceback:
	[string "function cal_acc_rule(dataset)..."]:3: in function 'cal_acc_rule'
	[string "print ('accuracy on train set '..cal_acc_rule..."]:1: in main chunk
	[C]: in function 'xpcall'
	/Users/YRZ/torch/install/share/lua/5.1/itorch/main.lua:210: in function </Users/YRZ/torch/install/share/lua/5.1/itorch/main.lua:174>
	/Users/YRZ/torch/install/share/lua/5.1/lzmq/poller.lua:75: in function 'poll'
	/Users/YRZ/torch/install/share/lua/5.1/lzmq/impl/loop.lua:307: in function 'poll'
	/Users/YRZ/torch/install/share/lua/5.1/lzmq/impl/loop.lua:325: in function 'sleep_ex'
	/Users/YRZ/torch/install/share/lua/5.1/lzmq/impl/loop.lua:370: in function 'start'
	/Users/YRZ/torch/install/share/lua/5.1/itorch/main.lua:389: in main chunk
	[C]: in function 'require'
	(command line):1: in main chunk
	[C]: at 0x010b22c360: 

In [25]:
mislabeled_rule = {}
local output
for i = 1, newtestset:size() do
    local output = simple_rule(newtestset[i][1])
    if output ~= newtestset[i][2] then
        table.insert(mislabeled_rule, { data_id = i, pred = output, gt = newtestset[i][2]})
    end
end

[string "mislabeled_rule = {}..."]:3: attempt to call method 'size' (a nil value)
stack traceback:
	[string "mislabeled_rule = {}..."]:3: in main chunk
	[C]: in function 'xpcall'
	/Users/YRZ/torch/install/share/lua/5.1/itorch/main.lua:210: in function </Users/YRZ/torch/install/share/lua/5.1/itorch/main.lua:174>
	/Users/YRZ/torch/install/share/lua/5.1/lzmq/poller.lua:75: in function 'poll'
	/Users/YRZ/torch/install/share/lua/5.1/lzmq/impl/loop.lua:307: in function 'poll'
	/Users/YRZ/torch/install/share/lua/5.1/lzmq/impl/loop.lua:325: in function 'sleep_ex'
	/Users/YRZ/torch/install/share/lua/5.1/lzmq/impl/loop.lua:370: in function 'start'
	/Users/YRZ/torch/install/share/lua/5.1/itorch/main.lua:389: in main chunk
	[C]: in function 'require'
	(command line):1: in main chunk
	[C]: at 0x010b22c360: 

In [26]:
print(#mislabeled_rule)

In [27]:
print(mislabeled_rule)

In [28]:
local i = 1.5
local x = torch.Tensor{i, i * i}:reshape(1,2)
print(x)

{
}


 1.5000  2.2500
[torch.DoubleTensor of size 1x2]



In [29]:
function make_linear_spine(vec, targetLen)
    local len = (#vec)[1]
    local ys = {}
    
    for i = 1, len do
        table.insert(ys, vec[i])
    end
    
    local res = torch.Tensor(targetLen)
    
    local i = 1
    for ind = 1, targetLen do
        local x = (ind - 1) * (len - 1) / (targetLen - 1) + 1
        if  x > i then
            i = i + 1
        end
        if x == i then 
            res[ind] = ys[i]
        else
            res[ind] = (ys[i] - ys[i - 1]) * (x - i + 1) + ys[i - 1]
        end
    end
    return res
end

In [30]:
-- print(peek)
print(make_linear_spine(peek, 64))
-- fit_quad(peek)

[string "function make_linear_spine(vec, targetLen)..."]:2: nn.TemporalConvolution has no length operator
stack traceback:
	[C]: in function '__len'
	[string "function make_linear_spine(vec, targetLen)..."]:2: in function 'make_linear_spine'
	[string "-- print(peek)..."]:2: in main chunk
	[C]: in function 'xpcall'
	/Users/YRZ/torch/install/share/lua/5.1/itorch/main.lua:210: in function </Users/YRZ/torch/install/share/lua/5.1/itorch/main.lua:174>
	/Users/YRZ/torch/install/share/lua/5.1/lzmq/poller.lua:75: in function 'poll'
	/Users/YRZ/torch/install/share/lua/5.1/lzmq/impl/loop.lua:307: in function 'poll'
	/Users/YRZ/torch/install/share/lua/5.1/lzmq/impl/loop.lua:325: in function 'sleep_ex'
	/Users/YRZ/torch/install/share/lua/5.1/lzmq/impl/loop.lua:370: in function 'start'
	/Users/YRZ/torch/install/share/lua/5.1/itorch/main.lua:389: in main chunk
	[C]: in function 'require'
	(command line):1: in main chunk
	[C]: at 0x010b22c360: 

In [24]:
function toTable(vec)
    local tmp = {}
    for i = 1, (#vec)[1] do
       tmp[i] = vec[i] 
    end
    return tmp
end
local cjosn = require 'cjson'
function makeJson(indata)
    local k = (#indata.data)[1]
    local aryDatas = {}
    for i = 1, k do
        aryDatas[i] = {}
        aryDatas[i]["label"] = indata.label[i]
        aryDatas[i]["input"] = toTable(indata.data[{i, {}, 1}])
    end
    return aryDatas
end
local jsonTable = {};
jsonTable['train'] = makeJson(trainset)
jsonTable['test'] = makeJson(testset)
jsonTable['test_new'] = makeJson(newtestset)
local jsonStr = cjson.encode(jsonTable)
print(jsonStr)
-- file = io.open("data_quad.json", "a")
-- file:write(jsonStr)

{"test":[{"input":[-0.31645411252975,-0.28409284353256,-0.25281038880348,-0.2226088643074,-0.19348613917828,-0.16544362902641,-0.13848131895065,-0.11259784549475,-0.087795257568359,-0.064071498811245,-0.041427943855524,-0.019863907247782,0.0006199263734743,0.020024243742228,0.038348354399204,0.055593643337488,0.071758031845093,0.086843602359295,0.10084895789623,0.11377411335707,0.12561975419521,0.13638587296009,0.14607249200344,0.15467889606953,0.16220577061176,0.16865245997906,0.1740196198225,0.17830657958984,0.1815140247345,0.18364195525646,0.18469037115574,0.18465788662434,0.18354658782482,0.18135507404804,0.17808404564857,0.17373350262642,0.16830275952816,0.16179180145264,0.154202029109,0.14553134143353,0.13578183948994,0.12495213747025,0.11304292082787,0.10005348920822,0.08598455041647,0.070836089551449,0.054607428610325,0.037299249321222,0.018910864368081,-0.00055703532416373,-0.021104451268911,-0.042732071131468,-0.065439209342003,-0.089225858449936,-0.11409271508455,-0.14003978

124,0.16113178431988,0.16020984947681,0.15834592282772,0.15554001927376,0.15179142355919,0.14710086584091,0.14146761596203,0.1348916888237,0.12737379968166,0.11891390383244,0.10951065272093,0.099166102707386,0.087878882884979,0.075648985803127,0.062477108091116,0.048362549394369,0.033306010067463,0.017306797206402,0.00036490650381893,-0.01751896739006,-0.036344826221466,-0.056113358587027,-0.076823875308037,-0.098477065563202,-0.12107293307781,-0.14461079239845,-0.16909131407738,-0.19451382756233,-0.22087900340557,-0.248186185956,-0.2764353454113,-0.3056278526783,-0.33576235175133],"label":1},{"input":[0.12517260015011,0.11873491108418,0.1124160811305,0.10621612519026,0.10013642162085,0.094174906611443,0.088332943618298,0.082610547542572,0.07700701802969,0.071523055434227,0.066158652305603,0.060912430286407,0.055786464363337,0.050779365003109,0.045891139656305,0.04112247377634,0.036473371088505,0.031943142414093,0.027531780302525,0.02323998324573,0.01906774751842,0.015014382079244,0.01

58552980422974,-0.057134129106998,-0.055528677999973,-0.053736627101898,-0.051758669316769,-0.049594111740589,-0.047243643552065],"label":1},{"input":[-0.030370863154531,-0.031942449510098,-0.033391017466784,-0.034717258065939,-0.035920482128859,-0.037001382559538,-0.037959259003401,-0.038794122636318,-0.039506658911705,-0.040096867829561,-0.040564056485891,-0.040908228605986,-0.04113007709384,-0.041228905320168,-0.041205406188965,-0.041059583425522,-0.040790740400553,-0.040398880839348,-0.039884693920612,-0.039247490465641,-0.038487959653139,-0.037605412304401,-0.036600537598133,-0.035472642630339,-0.034222424030304,-0.032849188894033,-0.031352933496237,-0.02973435074091,-0.027993442490697,-0.026129517704248,-0.024143263697624,-0.022033995017409,-0.019801706075668,-0.017447091639042,-0.014970150776207,-0.012370192445815,-0.0096472157165408,-0.006801912561059,-0.0038335914723575,-0.00074294413207099,0.0024707210250199,0.0058067128993571,0.0092650316655636,0.012847058475018,0.0165507216

24697208405,-0.56055408716202,-0.53853118419647,-0.5151778459549,-0.49049445986748,-0.46448069810867,-0.43713656067848,-0.40846237540245,-0.37845781445503,-0.34712284803391,-0.31445816159248,-0.280463129282,-0.24513700604439,-0.20848117768764,-0.17049564421177,-0.13117904961109,-0.090532749891281,-0.048555370420218,-0.0052482951432467,0.039389166980982,0.085356332361698,0.13265457749367,0.18128250539303,0.2312408387661,0.28252956271172,0.33514866232872,0.3890974521637,0.4443773329258,0.50098693370819,0.55892688035965,0.6181972026825,0.67879724502563,0.7407283782959,0.80398923158646,0.8685804605484,0.93450206518173,1.0017540454865,1.0703357458115,1.1402485370636,1.2114909887314,1.2840638160706,1.3579664230347,1.4332000017166,1.5097633600235,1.5876576900482],"label":2},{"input":[-0.88046824932098,-0.87585198879242,-0.87010675668716,-0.86323261260986,-0.85522919893265,-0.84609651565552,-0.83583492040634,-0.82444405555725,-0.8119238615036,-0.79827475547791,-0.78349673748016,-0.767589092254

277713298798,1.5090037584305,1.5916702747345,1.6757695674896,1.761302113533],"label":2},{"input":[-0.86745393276215,-0.8661795258522,-0.86363452672958,-0.85981822013855,-0.85473161935806,-0.84837377071381,-0.84074527025223,-0.8318458199501,-0.8216757774353,-0.81023478507996,-0.79752284288406,-0.78353995084763,-0.76828646659851,-0.75176233053207,-0.73396694660187,-0.71490091085434,-0.69456428289413,-0.67295634746552,-0.65007781982422,-0.62592869997025,-0.60050857067108,-0.57381755113602,-0.54585552215576,-0.51662296056747,-0.486119389534,-0.45434522628784,-0.42129975557327,-0.38698402047157,-0.35139736533165,-0.31453973054886,-0.27641114592552,-0.23701161146164,-0.19634181261063,-0.15440037846565,-0.11118867248297,-0.066706016659737,-0.020952405408025,0.026071462780237,0.074366979300976,0.12393274903297,0.1747694760561,0.22687716782093,0.28025579452515,0.33490470051765,0.39082524180412,0.4480160176754,0.50647777318954,0.56621050834656,0.62721413373947,0.68948805332184,0.75303292274475,0

...

0.024506576359272,-0.036867570132017,-0.049800209701061,-0.063304491341114,-0.077380627393723,-0.092028208076954,-0.10724762827158],"label":4},{"input":[-0.29283982515335,-0.28320074081421,-0.2735783457756,-0.26397225260735,-0.25438287854195,-0.24481020867825,-0.23525404930115,-0.22571438550949,-0.2161912471056,-0.2066848129034,-0.19719487428665,-0.18772166967392,-0.17826496064663,-0.16882476210594,-0.1594010591507,-0.14999407529831,-0.14060360193253,-0.1312298476696,-0.12187258154154,-0.11253183335066,-0.10320779681206,-0.093900062143803,-0.084609247744083,-0.07533472776413,-0.066076926887035,-0.056835625320673,-0.04761104285717,-0.038402963429689,-0.029211392626166,-0.020036531612277,-0.010878180153668,-0.0017363351071253,0.007388798519969,0.016497425734997,0.025589544326067,0.034664951264858,0.043723851442337,0.052766244858503,0.061791926622391,0.070801101624966,0.079793766140938,0.088769726455212,0.097729168832302,0.10667211562395,0.11559834331274,0.12450806051493,0.13340127468109,

475559473,0.017804363742471,0.0085924128070474,-0.00058917189016938,-0.0097403917461634,-0.018861448392272,-0.027952142059803,-0.037012673914433,-0.046042837202549,-0.055042635649443,-0.06401227414608,-0.072951547801495,-0.081860452890396,-0.090739198029041,-0.099587582051754,-0.10840559750795,-0.11719344556332,-0.12595093250275,-0.13467805087566,-0.14337500929832,-0.15204180777073,-0.16067804396152,-0.1692841053009,-0.17785981297493,-0.18640534579754,-0.1949205249548,-0.20340533554554,-0.21185998618603,-0.22028426826,-0.22867839038372,-0.23704193532467,-0.24537552893162,-0.25367856025696,-0.26195141673088,-0.27019390463829,-0.27840626239777],"label":4},{"input":[0.31742241978645,0.3188459277153,0.31971287727356,0.32002347707748,0.3197774887085,0.31897515058517,0.31761625409126,0.3157009780407,0.31322914361954,0.31020075082779,0.30661597847939,0.30247485637665,0.29777717590332,0.2925229370594,0.28671231865883,0.28034514188766,0.27342161536217,0.26594153046608,0.25790506601334,0.2493120

41929292678833,0.41391131281853,0.40814614295959,0.4019972383976,0.39546456933022,0.38854816555977,0.38124823570251,0.37356474995613,0.36549732089043,0.35704633593559,0.34821161627769,0.33899334073067,0.32939133048058,0.3194055557251,0.30903625488281,0.29828321933746,0.28714641928673,0.27562606334686,0.26372200250626,0.25143414735794,0.23876278102398,0.22570766508579,0.21226899325848,0.1984465867281,0.18424043059349,0.16965053975582,0.15467709302902,0.139319896698,0.12357916682959,0.10745447874069,0.090946458280087,0.07405448704958,0.056778971105814,0.039119709283113,0.021076906472445,0.0026503566186875,-0.016159940510988,-0.035353779792786,-0.054931364953518,-0.074892699718475,-0.095237568020821,-0.11596619337797,-0.13707855343819,-0.15857446193695,-0.18045412003994,-0.20271752774715,-0.22536447644234,-0.24839515984058,-0.27180960774422,-0.29560759663582,-0.31978932023048,-0.34435456991196,-0.36930379271507,-0.39463636279106,-0.42035287618637,-0.44645291566849,-0.47293671965599,-0.499

.12116052210331,0.10404987633228,0.08570709079504,0.066132359206676,0.045325476676226,0.023286454379559,1.5488434655708e-05,-0.024487419053912,-0.050222471356392,-0.077189669013023,-0.10538881272078,-0.13482010364532,-0.16548332571983,-0.1973787099123,-0.2305062264204,-0.26486569643021,-0.30045709013939,-0.33728063106537,-0.37533634901047,-0.41462397575378,-0.4551437497139,-0.49689549207687,-0.53987938165665,-0.58409529924393,-0.62954324483871],"label":4},{"input":[0.46315211057663,0.45952332019806,0.45535877346992,0.45065823197365,0.44542190432549,0.43964982032776,0.43334174156189,0.42649790644646,0.41911807656288,0.41120246052742,0.40275087952614,0.39376351237297,0.38424035906792,0.37418124079704,0.36358633637428,0.35245543718338,0.34078878164291,0.32858633995056,0.31584790349007,0.30257350206375,0.28876352310181,0.27441737055779,0.25953564047813,0.24411791563034,0.22816421091557,0.21167473495007,0.19464947283268,0.17708824574947,0.15899123251438,0.1403584331274,0.1211896687746,0.101

2581558227539,0.41293269395828,0.39966928958893,0.38602519035339,0.372000426054,0.35759493708611,0.34280878305435,0.32764193415642,0.31209459900856,0.29616659879684,0.27985787391663,0.26316848397255,0.24609839916229,0.22864781320095,0.21081654727459,0.19260460138321,0.17401196062565,0.15503862500191,0.13568480312824,0.11595029383898,0.095835097134113,0.075339213013649,0.054462634027004,0.033205572515726,0.011567822657526,-0.010450821369886,-0.032849747687578,-0.055629566311836,-0.078790076076984,-0.10233107209206,-0.12625275552273,-0.15055513381958,-0.17523819208145,-0.20030173659325,-0.22574618458748,-0.25157111883163,-0.27777671813965,-0.30436283349991,-0.33132982254028,-0.35867729783058,-0.38640567660332,-0.41451454162598,-0.44300389289856,-0.47187411785126,-0.5011248588562,-0.53075647354126,-0.56076854467392,-0.5911613702774,-0.62193465232849,-0.65308880805969,-0.68462347984314,-0.71653878688812,-0.74883484840393,-0.78151160478592],"label":4},{"input":[0.63333535194397,0.6162208318

## Subtle Adjustment

In [47]:
function make_adjset(name, mode)
    local ldr = Loader:new(nil, 256)
    local collection = {data = ldr.data[name]:float(), label = ldr.label[name]}
    function collection:size() 
        return self.data:size(1) 
    end
    
    -- Mel Frequency
    for j = 1, collection:size() do
        collection.data[{j, {}, 1}]:div(700):log1p():mul(5975.208)
    end
    
    -- local standardization
    for i = 1, 2 do
        for j = 1, collection:size() do
            local std = collection.data[{j, {}, i}]:std()
            collection.data[{j, {}, i}]:div(std)
        end
    end

    -- global standardization
    for i = 1, 2 do
        local std = collection.data[{{}, {}, i}]:std()
        collection.data[{{}, {}, i}]:div(std)
    end

    local resized_collection = {
        data = torch.Tensor(collection:size(), max_len,2):float(),
        label = collection.label
    }
    -- filter noice and shif to the beginning
    local coef = {}
    for i = 1, collection:size() do
        for j = 1, 256 do
            if (collection.data[{i, j, 2}] < 1.0) then
                collection.data[{i, j, 1}] = 0.0
                collection.data[{i, j, 2}] = 0.0
            end
        end
        local shifted_F0 = torch.Tensor(max_len):fill(0.0)
        local shifted_Engy = torch.Tensor(max_len):fill(0.0)
        local data = collection.data[{i, {}, {}}]
        local tmpF0 = data[{{}, 1}][data[{{}, 1}]:gt(0.0)]:clone()
        local tmpEngy = data[{{}, 2}][data[{{}, 2}]:gt(0.0)]:clone()
        
        peek = tmpF0
        
--         smooth (refer to a paper)
        local c_1 = 0.3
        local c_2 = 0.5
        local delind
        local nowlen = (#tmpF0)[1]
        _, delind = torch.max(tmpF0, 1)
        for j = 1, (#delind)[1] do
            if nowlen - delind[j] < 0.1 * nowlen or delind[j] < 0.1 * nowlen then
                tmpF0[delind[j]] = 0
            end
        end
        tmpF0 = tmpF0[tmpF0:gt(0.0)]
        _, delind = torch.min(tmpF0, 1)
        for j = 1, (#delind)[1] do
            if nowlen - delind[j] < 0.1 * nowlen or delind[j] < 0.1 * nowlen then
                tmpF0[delind[j]] = 0
            end
        end
        tmpF0 = tmpF0[tmpF0:gt(0.0)]
        
        tmpF0 = tmpF0:index(1 ,torch.linspace((#tmpF0)[1],1,(#tmpF0)[1]):long())
        local tmpF0_prime = tmpF0:clone()
        -- half or double
        for j = 2, (#tmpF0)[1] do
            if math.abs(tmpF0[j] / 2 - tmpF0[j - 1]) < c_1 then 
                tmpF0[j] = tmpF0[j] / 2
            elseif math.abs(2 * tmpF0[j] - tmpF0[j - 1]) < c_1 then
                tmpF0[j] = tmpF0[j] * 2
            end
        end
        -- random error
        for j = 3, (#tmpF0)[1] - 1 do
            if math.abs(tmpF0[j] - tmpF0_prime[j - 1]) > c_1 and math.abs(tmpF0[j + 1] - tmpF0_prime[j - 1]) > c_2 then
                tmpF0_prime[j] = 2 * tmpF0_prime[j - 1] - tmpF0_prime[j - 2]
            elseif math.abs(tmpF0[j] - tmpF0_prime[j - 1]) > c_1 and math.abs(tmpF0[j + 1] - tmpF0_prime[j - 1]) <= c_2 then
                tmpF0_prime[j] = 0.5 * (tmpF0_prime[j - 1] + tmpF0[j + 1])
            else 
                tmpF0_prime[j] = tmpF0[j] 
            end
        end
        -- backward check
        for j = (#tmpF0)[1] - 2, 2, -1 do
            if math.abs(tmpF0_prime[j] - tmpF0_prime[j + 1]) > c_1 and math.abs(tmpF0_prime[j - 1] - tmpF0_prime[j + 1]) > c_2 then
                tmpF0[j] = 2 * tmpF0_prime[j + 1] - tmpF0_prime[j + 2]
            elseif math.abs(tmpF0_prime[j] - tmpF0_prime[j - 1]) > c_1 and math.abs(tmpF0_prime[j + 1] - tmpF0_prime[j - 1]) <= c_2 then
                tmpF0[j] = 0.5 * (tmpF0_prime[j + 1] + tmpF0_prime[j - 1])
            else 
                tmpF0[j] = tmpF0_prime[j]
            end
            if math.abs(tmpF0_prime[j] - tmpF0[j]) < c_1 then
                for k = 1, j - 1 do
                    tmpF0[k] = tmpF0_prime[k]
                end
                break
            end
        end
--         tmpF0:index(1 ,torch.linspace((#tmpF0)[1],1,(#tmpF0)[1]):long())
        
--         tmpF0 = kick(tmpF0, 1, 0)
--         tmpEngy = kick(tmpEngy, 1, 0)
        
--         local cut_len = (#tmpF0)[1] * 0.25
--         tmpF0 = tmpF0[{{cut_len, -1}}]

        -- smooth
        tmpF0 = moving_avg(tmpF0, 5)
        tmpF0 = tmpF0[tmpF0:gt(0.0)]:clone()
        tmpEngy = moving_avg(tmpEngy, 5)
        tmpEngy = tmpEngy[tmpEngy:gt(0.0)]:clone()

        if mode == 'shift' then
            shifted_F0[{{2, (#tmpF0)[1] + 1}}] = tmpF0
            shifted_Engy[{{2, (#tmpEngy)[1] + 1}}] = tmpEngy
            resized_collection.data[{i, {}, 1}] = shifted_F0
            resized_collection.data[{i, {}, 2}] = shifted_Engy
        elseif mode == 'quad' then
            resized_collection.data[{i, {}, 1}], coef[i] = fit_quad(tmpF0, max_len)
            resized_collection.data[{i, {}, 2}] = fit_quad(tmpEngy, max_len)
        elseif mode == 'linear' then
            resized_collection.data[{i, {}, 1}] = make_linear_spine(tmpF0, max_len)
            resized_collection.data[{i, {}, 2}] = make_linear_spine(tmpEngy, max_len)
        end
    end
--     for i = 1, 2 do
--         for j = 1, dataset:size() do
--             local std = resized_collection.data[{j, {}, i}]:std()
--             resized_collection.data[{j, {}, i}]:div(std)
--         end
--     end
    for i = 1, 2 do
        for j = 1, collection:size() do
            local mean = resized_collection.data[{j, {}, i}]:mean()
            resized_collection.data[{j, {}, i}]:csub(mean)
--             local mean = resized_collection.data[{j, {}, i}][-1]
--             resized_collection.data[{j, {}, i}]:csub(mean)
--             local std = resized_collection.data[{{}, {}, i}]:std()
--             resized_collection.data[{{}, {}, i}]:div(std)
        end
    end
    for i = 1, 2 do
        local std = resized_collection.data[{{}, {}, i}]:std()
        resized_collection.data[{{}, {}, i}]:div(std)
    end
    
    resized_collection.data[{{}, {}, 2}]:fill(0.0)
    for i = 1, collection:size() do
        resized_collection[i] = {resized_collection.data[i], resized_collection.label[i]}
    end
    print("dataset "..name.." has been constructed!")
    return resized_collection, coef
end

In [48]:
adjnewtestset, adjnewtestcoef = make_adjset('test_new', 'linear')

dataset test_new has been constructed!	


In [49]:
local x = torch.range(1,64)
local y = adjnewtestset[7][1][{{},1}]
Plot():line(x, y,'f0'):draw()